In [1]:
import pandas as pd
import requests
from bs4 import BeautifulSoup
import json
import csv
import re
import os
import xml.etree.ElementTree as et
from urllib.request import urlopen
import datetime
import time
from tqdm import tqdm

In [2]:
dirname = os.path.dirname(os.path.abspath("podcast_list.csv"))
filename = os.path.join(dirname, 'podcast_list.csv')

print(filename)

/Users/garyhu/Desktop/Georgia Tech/Classes/CSE 6242/Project/data/podcast_list.csv


In [3]:
podcasts = pd.read_csv(filename, index_col = False)
podcasts.head()

Name          ID
0            Audio Poem of the Day   270054094
1                 Hard Men Podcast  1512510969
2                  The Great Books  1281089527
3  Dressed: The History of Fashion  1350850605
4            When Meghan Met Harry  1327426491

In [4]:
feed_urls_file = os.path.join(dirname, 'feedURL_need_episode_details.csv')
feeds = pd.read_csv(feed_urls_file, index_col = False)

feeds.head()

id country                                      FeedURL
0   270054094      us        https://feeds.simplecast.com/p7Q9jZ0K
1  1512510969      us     https://feeds.buzzsprout.com/1068361.rss
2  1281089527      us  https://feeds.podcastmirror.com/great-books
3  1350850605      us           https://feeds.megaphone.fm/dressed
4  1327426491      us      http://feeds.megaphone.fm/PPY8228198655

In [5]:
len(feeds.index)

13023

In [6]:
test_file = os.path.join(dirname, 'podcast_feeds_test.csv')
feeds_test = pd.read_csv(test_file, index_col = False)


feeds_test.head()
    

id country                                      FeedURL
0   270054094      us        https://feeds.simplecast.com/p7Q9jZ0K
1  1512510969      us     https://feeds.buzzsprout.com/1068361.rss
2  1281089527      us  https://feeds.podcastmirror.com/great-books
3  1350850605      us           https://feeds.megaphone.fm/dressed

In [7]:
def get_details(feed_url, podcast_id):
    
    resp = requests.get(feed_url)
    bs = BeautifulSoup(resp.content, features='xml')
    
    def cleanhtml(raw_html):
        cleaner = re.compile('<.*?>')
        clean_text = re.sub(cleaner, '', raw_html)
        return clean_text
    
    def hhmmss_sec(time_str):
        h, m, s = time_str.split(':')
        return int(h) * 3600 + int(m) * 60 + int(s)
    
    def mmss_sec(time_str):
        m, s = time_str.split(':')
        return int(m) * 60 + int(s)

    items = bs.findAll('item')
    
    show_items = []
    
    for index, item in enumerate(items):
        episode = {}
        episode['podcast_id'] = podcast_id
        episode['title'] = item.title.text if item.title is not None else None
        episode['description'] = cleanhtml(item.description.text) if item.description is not None else None

        try:
            if ":" in item.duration.text:
                dur_time = item.duration.text
                dur_list = item.duration.text.split(':')

                if len(dur_list) == 3:
                    episode['duration'] = hhmmss_sec(dur_time)

                if len(dur_list) == 2:
                    episode['duration'] = mmss_sec(dur_time)

            else:
                episode['duration'] = item.duration if item.duration is not None else None
        except:
            print("podcast_id = ",podcast_id, " feed_url = ", feed_url, " row number = ", index, " Duration issue")
            pass
        episode['pubDate'] = item.pubDate.text if item.pubDate is not None else None      
        show_items.append(episode)
    
    df_cols = ["podcast_id", "title", "description", "duration", "pubDate"]
    
    df = pd.DataFrame(show_items, columns = df_cols)

    return df

# get_details('http://feed.podbean.com/zibbyowens/feed.xml', "270054094")



In [8]:
def concat_all_shows(feeds):
    df_list = []

    for index, rows in tqdm(feeds.iterrows()):
        feed_url = rows["FeedURL"]
        podcast_id = rows["id"]
        
        try:
            df = get_details(feed_url, podcast_id)
            df_list.append(df)
        
        except:
            print(podcast_id, feed_url, "URL Error")
            pass

    final_output = pd.concat(df_list)
    
    return final_output

df_test = concat_all_shows(feeds_test)
df_test

4it [00:00,  8.88it/s]


podcast_id                                              title  \
0     270054094                                        The Red Sea   
1     270054094                            To Arielle and the Moon   
2     270054094                                          Late Melt   
3     270054094                                     Life of Savage   
4     270054094                                         Misgivings   
..          ...                                                ...   
234  1350850605               Branded: A History of Designer Logos   
235  1350850605        Freeing the Body: The Birth of Modern Dress   
236  1350850605  Founding Father of Haute Couture: Charles Fred...   
237  1350850605                              Dressed: Episode Zero   
238  1350850605        Introducing Dressed: The History of Fashion   

                                           description duration  \
0                                   By Stephen Edgar\n      174   
1                                  By David Trinidad\n       87   
2                                  By Melissa Broder\n       60   
3                                  By Vijay Seshadri\n      121   
4                                By William Matthews\n       85   
..                                                 ...      ...   
234  Logos and monograms are used by luxury fashion...   [2260]   
235  This week we explore the birth of modern dress...   [2252]   
236  This episode explores the career and legacy of...   [4055]   
237  Fashion history is about more than pretty clot...    [288]   
238  Every week, fashion historians April Calahan a...    [124]   

                             pubDate  
0    Sun, 21 Mar 2021 17:00:00 +0000  
1    Sat, 20 Mar 2021 17:00:00 +0000  
2    Fri, 19 Mar 2021 17:00:00 +0000  
3    Thu, 18 Mar 2021 17:00:00 +0000  
4    Wed, 17 Mar 2021 17:00:00 +0000  
..                               ...  
234  Tue, 13 Mar 2018 10:00:03 -0000  
235  Tue, 06 Mar 2018 11:00:02 -0000  
236  Tue, 27 Feb 2018 11:00:03 -0000  
237  Fri, 23 Feb 2018 17:23:00 -0000  
238  Tue, 20 Feb 2018 16:02:00 -0000  

[390 rows x 5 columns]

In [9]:
# df = concat_all_shows(feeds)
# df.to_csv('all_episode_details.csv', index=False, encoding = 'utf-8')

35it [00:07,  3.80it/s]

podcast_id =  1366633318  feed_url =  https://zibbyowens.podbean.com/feed.xml  row number =  414  Duration issue


37it [00:09,  2.39it/s]

podcast_id =  566908883  feed_url =  https://tangent.libsyn.com/rss  row number =  132  Duration issue


47it [00:12,  4.24it/s]

...

12960it [1:16:23,  2.29it/s]

podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  0  Duration issue
podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  1  Duration issue
podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  2  Duration issue
podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  3  Duration issue
podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  4  Duration issue
podcast_id =  549826354  feed_url =  http://feeds.feedburner.com/nhscouchto5kplus  row number =  5  Duration issue


12989it [1:16:30,  2.61it/s]

podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  49  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  56  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  57  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  59  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  63  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  66  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  68  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  71  Duration issue
podcast_id =  1535809341  feed_url =  https://jbpod.libsyn.com/applepodcast  row number =  76  Duration issue
podcast_id

13023it [1:16:38,  2.83it/s]


In [10]:
results = df
len(results.index)

1561563

In [14]:
import numpy as np

results_1 = results[0:250000]
results_2 = results[250001:500000]
results_3 = results[500001:750000]
results_4 = results[750001:1000000]
results_5 = results[1000001:1250000]
results_6 = results[1250001:1500000]
results_7 = results[1500001:-1]

results_1.to_csv('all_episode_details_1.csv', index=False, encoding = 'utf-8')
results_2.to_csv('all_episode_details_2.csv', index=False, encoding = 'utf-8')
results_3.to_csv('all_episode_details_3.csv', index=False, encoding = 'utf-8')
results_4.to_csv('all_episode_details_4.csv', index=False, encoding = 'utf-8')
results_5.to_csv('all_episode_details_5.csv', index=False, encoding = 'utf-8')
results_6.to_csv('all_episode_details_6.csv', index=False, encoding = 'utf-8')
results_7.to_csv('all_episode_details_7.csv', index=False, encoding = 'utf-8')

In [15]:
missing_duration = results['duration'].isnull().sum()
print(missing_duration)

33424


In [17]:
check = results[results['podcast_id'] == 343580439]
display(check)

podcast_id                                           title  \
0    343580439  Introducing Robin Ince’s Laws That Aren’t Laws   
1    343580439                               A History of Rock   
2    343580439                     The Fundamentals of Reality   
3    343580439                          The Science of Cooking   
4    343580439                                    Neanderthals   
..         ...                                             ...   
142  343580439                                 Popular Science   
143  343580439                            Science and Religion   
144  343580439                                 Quantum Physics   
145  343580439                           Extraterrestrial Life   
146  343580439                           Science and Comedians   

                                           description duration  \
0    Robin explores the origins of laws that seem t...    [915]   
1    A History of Rock\n\nBrian Cox and Robin Ince ...   [2551]   
2    The Fundamentals of Reality\n\nBrian Cox and R...   [2478]   
3    The Science of Cooking\n\nBrian Cox and Robin ...   [2607]   
4    The Neanderthals\n\nBrian Cox and Robin Ince a...   [2338]   
..                                                 ...      ...   
142  Physicist Brian Cox and comedian Robin Ince re...   [1685]   
143  Physicist Brian Cox and comedian Robin Ince ta...   [1511]   
144  Physicist Brian Cox and comedian Robin Ince ta...   [1513]   
145  Series in which physicist Brian Cox and comedi...   [1511]   
146  Former cosmologist Dara O'Briain and Dr Alice ...   [1509]   

                             pubDate  
0    Wed, 10 Mar 2021 10:19:00 +0000  
1    Mon, 15 Feb 2021 16:30:00 +0000  
2    Mon, 08 Feb 2021 16:30:00 +0000  
3    Mon, 01 Feb 2021 16:30:00 +0000  
4    Mon, 25 Jan 2021 16:30:00 +0000  
..                               ...  
142  Mon, 14 Jun 2010 15:30:00 +0000  
143  Mon, 21 Dec 2009 16:30:00 +0000  
144  Mon, 14 Dec 2009 16:30:00 +0000  
145  Mon, 07 Dec 2009 16:30:00 +0000  
146  Mon, 30 Nov 2009 16:30:00 +0000  

[294 rows x 5 columns]

In [20]:
feed_urls_file2 = os.path.join(dirname, 'feedURL_need_episode_details2.csv')
feeds2 = pd.read_csv(feed_urls_file2, index_col = False)

print(len(feeds2.index))

8712


In [21]:
feeds2.head()

id                                            FeedURL
0   271446384  http://flyingpodcast.jellycast.com/podcast/feed/2
1  1532898519           https://feeds.captivate.fm/water-flying/
2  1554266407                     https://avicast.libsyn.com/rss
3  1351497073       http://www.airforceassoc.org/blog?format=rss
4  1451081782            https://anchor.fm/s/8e00904/podcast/rss

In [22]:
# results2 = concat_all_shows(feeds2)
# results2.to_csv('all_episode_details.csv', index=False, encoding = 'utf-8')

14it [00:06,  3.60it/s]

podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  0  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  1  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  2  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  3  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  4  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  5  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast.com/gravityconnect?format=rss  row number =  6  Duration issue
podcast_id =  1534355369  feed_url =  https://www.theparamotorpodcast

22it [00:07,  5.77it/s]

podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  0  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  1  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  2  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  3  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  4  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  5  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  6  Duration issue
podcast_id =  846897419  feed_url =  http://feeds.rapidfeeds.com/70069/  row number =  7  Duration issue


42it [00:13,  2.76it/s]

...

8514it [57:54,  1.44it/s]

podcast_id =  773888088  feed_url =  https://www.arresteddevops.com/episode/index.xml  row number =  2  Duration issue


8613it [58:12,  1.67it/s]

podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  62  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  63  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  92  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  104  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  114  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  119  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  135  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com/feed/podcast/  row number =  137  Duration issue
podcast_id =  1084020770  feed_url =  https://www.trailwentcold.com

8712it [58:26,  2.48it/s]


In [23]:
results_8 = results2[0:250000]
results_9 = results2[250001:500000]
results_10 = results2[500001:750000]
results_11 = results2[750001:1000000]
results_12 = results2[1000001:-1]


results_8.to_csv('all_episode_details_8.csv', index=False, encoding = 'utf-8')
results_9.to_csv('all_episode_details_9.csv', index=False, encoding = 'utf-8')
results_10.to_csv('all_episode_details_10.csv', index=False, encoding = 'utf-8')
results_11.to_csv('all_episode_details_11.csv', index=False, encoding = 'utf-8')
results_12.to_csv('all_episode_details_12.csv', index=False, encoding = 'utf-8')


In [24]:
print(len(results2))

1074970


In [25]:
final_results = pd.concat([results, results2])
print(len(results))
print(len(results2))
print(len(final_results))

1561563
1074970
2636533


In [27]:
feed_urls_file3 = os.path.join(dirname, 'feedURL_need_episode_details3.csv')
feeds3 = pd.read_csv(feed_urls_file3, index_col = False)

feeds3.head()

id                                   FeedURL
0  1408082097   https://anchor.fm/s/5631168/podcast/rss
1  1557235066  https://anchor.fm/s/4fbe65f0/podcast/rss
2  1092994298  https://anchor.fm/s/14cf51c0/podcast/rss
3  1452118040   https://thecelcast.podbean.com/feed.xml
4   827255972   https://anchor.fm/s/71eda00/podcast/rss

In [28]:
results3 = concat_all_shows(feeds3)

68it [00:22,  2.84it/s]

podcast_id =  1123253491  feed_url =  https://nwjeepcast.com/rss  row number =  127  Duration issue
podcast_id =  1123253491  feed_url =  https://nwjeepcast.com/rss  row number =  138  Duration issue
podcast_id =  1123253491  feed_url =  https://nwjeepcast.com/rss  row number =  143  Duration issue


70it [00:24,  1.38it/s]

podcast_id =  1083180382  feed_url =  http://www.wrenchnation.tv/feed/podcast/  row number =  30  Duration issue
podcast_id =  1083180382  feed_url =  http://www.wrenchnation.tv/feed/podcast/  row number =  35  Duration issue
podcast_id =  1083180382  feed_url =  http://www.wrenchnation.tv/feed/podcast/  row number =  49  Duration issue
podcast_id =  1083180382  feed_url =  http://www.wrenchnation.tv/feed/podcast/  row number =  168  Duration issue


83it [00:29,  3.25it/s]

...

267it [01:26,  2.41it/s]

podcast_id =  1032555599  feed_url =  http://galleycast.com/feed/podcast/  row number =  20  Duration issue


268it [01:29,  1.19s/it]

podcast_id =  1367495532  feed_url =  http://airlinepilotguy.com/feed/pt/  row number =  88  Duration issue
podcast_id =  1367495532  feed_url =  http://airlinepilotguy.com/feed/pt/  row number =  113  Duration issue
podcast_id =  1367495532  feed_url =  http://airlinepilotguy.com/feed/pt/  row number =  178  Duration issue
podcast_id =  1367495532  feed_url =  http://airlinepilotguy.com/feed/pt/  row number =  183  Duration issue
podcast_id =  1367495532  feed_url =  http://airlinepilotguy.com/feed/pt/  row number =  230  Duration issue


283it [01:31,  3.08it/s]


In [29]:
final_results = pd.concat([final_results, results3])

In [30]:
print(len(final_results))

2656564


In [129]:
results3.sample(10)

podcast_id  \
92   1092994298   
480   185237578   
30   1472650099   
298  1201374883   
484   903505596   
17   1513632985   
270  1042352601   
151   969802743   
13   1229949501   
107  1490906255   

                                                                                                                                      title  \
92                                                                                              Anime Arcade 44 – Summer 2017 Reviews Pt. 1   
480                                                                                Uncontrolled Airspace #161 "Endless Quest to Fill Space"   
30                                                                                                                    Ep.26 Don't be Trashy   
298                                                                                                      One Last Thing Before I Quit/Start   
484                                                                                                          166: Easy Up Sell - Headlights   
17   Episode 55: Delta and United pioneer quarantine-free international travel and we talk about traveling during COVID-19 times in general   
270                                                                                                      The Car Pro Show 06-23-18 (Hour 1)   
151                                                                                                                      #86 - Ninja Scroll   
13                                                                           Episode 078 | Pro training tips with Chad Fortenberry | Part 2   
107                                                                The INSANE Power of Kid Itachi Explained! Naruto Shippuden Anime / Manga   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       description  \
92                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [35]:
## Remove brackets from duration
final_results['duration'] = final_results['duration'].astype(str).map(lambda x: x.lstrip('[').rstrip(']'))
final_results.sample(10)

podcast_id                                              title  \
1    1161286064                       Situationships Feat. Danquai   
278  1143976129  Libra Horoscope for Leo Season (July 22 - Augu...   
90   1342021363  The WW Bro Podcast w/ Anthony DiDomenico: Epis...   
484  1101136985  Kevin Pietersen ‘the best to have ever played ...   
38    468609197                                         Episode 93   
221   312094772  1199: Leaving Scientology and Becoming an Ex-S...   
109  1088331670                          You Gotta Start Somewhere   
36   1529980714  Filmmaker Elegance Bratton (Pier Kids, My Hous...   
262   663379413                 Elon Musk: the Man Behind the Hype   
232   283605519                                 Anglo-Zanzibar War   

                                           description  \
1    Shop the Merch!\nhttps://www.brokegirltherapy....   
278  These horoscopes are month-ahead forecasts for...   
90   \nEpisode 74 of The WW Bro Podcast, this week ...   
484  Steve Harmison joined talkSPORT to react to th...   
38                     Episode 93 of the Internet Box.   
221  In today's episode of Mormon Stories Podcast w...   
109  Pete and Eric are joined by Garrett for our de...   
36   This week, John E. Kilberg interviews writer a...   
262  \n        At a time when Silicon Valley entrep...   
232  Zanzibar is a relatively tiny place, but its p...   

                                    duration                          pubDate  
1    <itunes:duration>3429</itunes:duration>  Sun, 27 Dec 2020 23:31:00 -0000  
278  <itunes:duration>1325</itunes:duration>    Mon, 22 Jul 2019 04:40:08 GMT  
90                                      4383  Mon, 24 Jun 2019 22:13:35 -0400  
484                                       70    Tue, 20 Mar 2018 12:59:43 GMT  
38                                      7177  Tue, 30 Jul 2013 07:22:16 +0000  
221                                     3701  Wed, 30 Oct 2019 08:00:00 +0000  
109                                     3296  Fri, 26 Feb 2016 06:00:00 +0000  
36                                    1744.0  Wed, 18 Nov 2020 07:00:00 +0000  
262                                     3214  Thu, 22 Oct 2015 19:51:38 -0000  
232  <itunes:duration>2059</itunes:duration>  Mon, 16 Mar 2020 13:00:00 -0000

In [37]:
final_results['duration'] = final_results['duration'].astype(str).map(lambda x: x.lstrip('<itunes:duration>').rstrip('</itunes:duration>'))


podcast_id                                              title  \
61    1251371805                   011-A love letter to my RAID log   
212   1491790492          Episode Twenty-Eight - The Power of Glove   
388    509309981  304: The Swamp Explained - Russian and Trump, ...   
470   1212068497                          Hour 1 - What Day Is It?    
144   1146086687  Ep 153: Volume vs. Intensity, RPE vs. Percenta...   
392   1524223075                     Gandhodak Mantra गंधोदक मन्त्र   
50    1513657225                              Sleepaway Camp (1983)   
59     355330932          How to Keep Your Grout Lines Clean | Tips   
55    1130708584                     232 - Opinions Don’t Pay Bills   
9     1551494225    Expat Life - Still Living Abroad After 12 Years   
50     358731231                                       Ask Joe #210   
34    1272423047     S3E59: Travel Schooling: Raise A Little Wonder   
109   1205668403                             Takes On Takes Ep. 112   
45     478352618                    #447 - All Hail King Deadpool!    
108    957265404  105: Brendan Poots – How a former punter pione...   
33    1509703697  Family Feeding Gift Guide: Katie's BLW Gift Picks   
149   1348074052    157. How to Stop Self-Sabotage with Dr. Judy Ho   
160    548674350  HPH141 : What is a structural engineer? – with...   
12     900015782  154: Hexagonal Thinking: A Colorful Tool for D...   
111   1163875124                                   Can you help me?   
149   1405059214        Ep. 024: Day 5-6 - Colorado Elk Hunt Series   
282   1408959075  11/04/19: Big Changes And Challenges At McDona...   
354   1067688314  1573: 9 Helpful Hints for making Good Decision...   
233   1193834591  Ep 85: Adulting with Social Media Strategist B...   
446    261109847  Episode 46: He Is My Master Volume 2 by Mattsu...   
301    327466681  How Klopp and Liverpool almost played it perfe...   
112    635045292   Vaccine Czar Makes Millions Based on False Data    
35    1491248459                                     Friend Request   
55     380278390  Transmute Mix - Another great month for melodi...   
78    1068940771  173. Sex Worker Rights with Alison Spittle and...   
109   1253570474                A Prayer to Offer Up in the Morning   
2330  1355495674  Tuesday MLB Previews, New York Jets Season Out...   
22    1534096260                         Episode 2 | "I'm Speaking"   
35     127782776                             Puntata del 09/03/2021   
16    1528050811  Resilience, Switching Concepts, and the Things...   
46    1457099403  S2E35: S2 E35 | Six Nations TV, Covid-19, Guin...   
899   1034379593  LOCKED ON LAKERS -- 4/14/17 -- Will Rob Pelink...   
46     717402509              Special Replay:  Life Skills For Kids   
140    279428154  Growth and solidarity: cities reimagining huma...   
7     1012713381       EP 151:  Point Creeps Talk About Point Creep   
489    523996362                    The Beerists 30 - The Mike Show   
38    1210250626  Episode 191: RECAP UFC Poirier vs Hooker | Jon...   
156   1498114990                                      Dejados Atrás   
30    1448223884  Brewery Financial Planning Q&A with Chris Farmand   
401   1092207516  Throwback Thursday: Got Junk? How to Get Rid o...   
166   1361914055  105: What If Your Thyroid Actually Is Your Pro...   
18    1538242507  Bobbi Brown Shares Advice For Aspiring Entrepr...   
376   1134941997  Locked on Hawks - Ep. 582 - Emergency Taurean ...   
370    498130432         RHONJ: The ICEmen Cometh - Live from Tampa   
545   1023150373  How Bad Are All These June Saints Injuries, To...   

                                            description duration  \
61    This episode, we talk about an old stand-by in...     2638   
212   Is Sean Murphy tipping pitches behind the dish...     1163   
388   In the second episode of our series "The Swamp...     4221   
470   Clay Travis reacts to Tom Brady literally losi...     2592   
144   In this episode, I answer questions su

In [43]:
final_results.sample(50)

podcast_id                                              title  \
568   1033048640                                     Get Rid of It?   
27    1305546061               123: A Conversation with Rachel Ross   
165    417051167                                       Genjo Koan 8   
70     548172803  Horror 101 - Episode XXXVIII: Alice, Sweet Ali...   
28    1471731529                           Birth Bag Must NOT Haves   
51    1413384728                    M&D 14: Sugaridoo - Irene Staal   
183   1382804627     Why Do Our Tax Dollars Support Unhealthy Food?   
431    327725953  Critical Hit #176: The Fen of Winters - Part 3...   
22    1237636223  177: Jenn Sherman's Yacht Rock Ride Removed an...   
11    1524346561                                Duyrikadeesh bhajan   
101   1360408159                                       GUYS NIGHT 4   
12    1495540957                        2WR 021: New Bikes and Gear   
39    1435277410        Why Women Ask: “What are you looking for?”    
168   1147459691  PES Intermedio 007 – Se me olvidaron las llave...   
161    919266944                         WCA #165 with Dave Collins   
69     307483087      Thursday 14th January Clyde 1 Superscoreboard   
9      975097372                           FYW 224: Nouveau vs Neuf   
13     868068396                           Stalin, little and large   
25    1083324677                       249: Closing the Arousal Gap   
69     482034476                 CarProUSA Podcast 9/26/2020 Hour 1   
96     120906714  SE-Radio Episode 356: Tim Coulter on Truffle, ...   
16    1485623466  Kenny Aronoff talks drumming for Mellencamp Se...   
56     435713106                            Barbara Taylor Bradford   
24    1507600269  Criminal Law: Crimes against property – Smuggling   
2     1360675823                                   Kettlebell Crazy   
470   1195967486  EFR 019: Framing Your Life's Vision with Zack ...   
16    1388645349                        12: Black Hawk Down, Part 2   
70     594960922  EY Cross-Border Taxation Spotlight for Week en...   
89    1445762076       [COSMIC CONNECTION] October Forecast + More    
24    1509241243                      Genetic Engineering of Humans   
236    510761000                         Stop Learning Through Pain   
781    215529509                                Fast Money 01/17/18   
230    354082588                                       Out Of Touch   
1058   902067712                                       Expectations   
397    911502027  Helping Young Women Understand Their Hormones ...   
733   1212734488  Survivor Heroes vs Healers vs Hustlers Episode...   
74    1441696714                  C.S. Lewis and the Empty Universe   
144   1509561884                            Help America talk again   
51    1336060206            Miami Heat: Late Loss to Boston Celtics   
11     607714950  Episode 22: Punks in Parkas - 2020 in Review P...   
120    677269882               Quarantine Basic with Dino-Ray Ramos   
77    1274217512  "My Business Was Hit Hard By COVID. What Do I ...   
138    290580703  TRC #486: Valentine’s Day Myths + Name That: V...   
71     989652832  276 Business Success in 2020 with the CEO of C...   
980   1271435757  Lance Roberts W Richard Rosso, Danny Ratliff O...   
111   1279955329  Pretty Little Podcasters with Janel Parrish & ...   
412    732915228                        What are Ultraterrestrials?   
6822  1355495674            Follow The Money | Mike Palm INT 022219   
62     951048357  Nurses leaving the NHS – the consequences of C...   
168   1199977889  78: Simon Sinek: How To Inspire Others To Do R...   

                                            description duration  \
568   Episode 348 - Does it serve me? That is an imp...      581   
27    This week, while Lindsie is away, Kail sits do...     4829   
165                 Please visit the forum thread here!    626.0   
70    "Your First Communion holds your last breath"\...     1925   
28    If you're like us, you like to be prep

In [80]:
import dateutil
from dateutil.relativedelta import *
from dateutil.easter import *
from dateutil.rrule import *
from dateutil.parser import *

def clean_pubdate(pubdate):
    try:
        date = dateutil.parser.parse(pubdate)
        date = str(date).split(" ")
        date = date[0]
    except:
        print('error', pubdate)
        date = pubdate
        pass

    return date

test_date = 'Thu, 17 Dec 2020 05:00:10 +0000'
test_date1 = 'Sat, 5 Mar 2011 11:00 PDT'
test_date2 = 'Fri, 02 Jun 2017 17:00:00 GMT'
test_date3 = '2016-12-12T00:00:00+00:00'
test_date4 = '2018-03-04'
test_date5 = 'January 5, 2009'
test_date6 = '12 Aug 2020 00:00 PST'
test_date7 = '7 Jul 2019 16:01:07 +0000'
test_date8 = 'June 1, 2017, 6:02 pm'
test_list = [test_date, test_date1, test_date2, test_date3, test_date4, test_date5, test_date6, test_date7, test_date8]

for test in test_list:
    print(clean_pubdate(test))

2020-12-17
2011-03-05
2017-06-02
2016-12-12
2018-03-04
2009-01-05
2020-08-12
2019-07-07
2017-06-01


In [151]:
final = pd.concat([results, results2, results3])
print(len(final))
final.sample(5)

2656564


podcast_id  \
382   458213762   
184  1195206601   
76    600106614   
149   814025804   
33   1453766984   

                                                                                              title  \
382                                                          Nuclear Hotseat #133: Sky Not Falling!   
184                                                                            Donald in Wonderland   
76   Mastering The Art Of Consulting Sales And Client Relationships With Andrew Sobel: Podcast #132   
149                                       Sex Gets Real 158: Messy sex, dating obsessed, & jealousy   
33                                                          The Revolution Begins at Home with Beth   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                            description  \
382                                                                                                                                                         

In [152]:
final_results_clean = final
final_results_clean['cleanDate'] = final['pubDate'].map(lambda x: clean_pubdate(x))
final_results_clean.sample(10)

/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname PDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname PST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname MST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  

error None
error Tues, 03 Mar 2020 17:56:00 GMT
error None
error None
error None
error None
error None


/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname CST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "


error None


/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname MDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "


...

/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname CDT identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "


error Thurs, 4 Mar 2021 12:00:00 GMT
error None
error None
error Thur, 21 May 2020 07:05:00 PDT
error Thur, 21 May 2020 07:00:00 PDT
error Thur, 30 April 2020 07:05:00 PDT
error Thur, 30 April 2020 07:00:00 PDT
error 
error 
error 
error 
error 
error 
error Thur, 17 January 2019 10:27:08 -0700
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error None
error Wed, 31 Feb 2018 13:30:00 EST
error Tues, 23 Feb 2021 16:00:00 GMT
error None


/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname CET identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "
/Users/garyhu/opt/anaconda3/lib/python3.8/site-packages/dateutil/parser/_parser.py:1213: UnknownTimezoneWarning: tzname CEST identified but not understood.  Pass `tzinfos` argument in order to correctly return a timezone-aware datetime.  In a future version, this will raise an exception.
  warnings.warn("tzname {tzname} identified but not understood.  "


error None
error 2017_12_09
error Tues, 22 Sept 2020 10:59:00 EST
error Thurs, 21 May 2020 10:59:00 EST
error None
error None
error None
error Tues, 09 Apr 2013 19:00:00 PST
error Thur, 13 Jun 2019 09:57:00 PDT
error Thu, 15 Sep 2005 00:00:00 GMT -07:00:00
error Sat, 17 Sep 2005 22:00:00 GMT -07:00:00
error Sat, 17 Sep 2005 23:00:00 GMT -07:00:00
error Thu, 29 Sep 2005 00:00:00 GMT -07:00:00
error Wed, 05 Oct 2005 00:00:00 GMT -07:00:00
error Wed, 12 Oct 2005 00:00:00 GMT -07:00:00
error Wed, 19 Oct 2005 00:00:00 GMT -07:00:00
error Wed, 26 Oct 2005 00:00:00 GMT -07:00:00
error Wed, 02 Nov 2005 00:00:00 GMT -07:00:00
error Wed, 09 Nov 2005 00:00:00 GMT -07:00:00
error Wed, 16 Nov 2005 01:00:00 GMT -07:00:00
error Wed, 23 Nov 2005 00:00:00 GMT -07:00:00
error Wed, 30 Nov 2005 00:00:00 GMT -07:00:00
error Wed, 07 Dec 2005 00:00:00 GMT -07:00:00
error Wed, 14 Dec 2005 00:00:00 GMT -07:00:00
error Wed, 21 Dec 2005 00:00:00 GMT -07:00:00
error Wed, 11 Jan 2006 00:00:00 GMT -07:00:00
error W

podcast_id  \
35   1547827376   
7    1509291370   
36    160904630   
78   1504169578   
287   190516844   
82   1153925147   
45    984527862   
9    1423288932   
135   995672024   
792   282795787   

                                                                                                                                                              title  \
35                                                                                                                                                 The Great Excuse   
7                                                                                                                                       27 Pandemic Insights Part 3   
36                                                                                                         My journey mapping the uncharted world | Tawanda Kanhema   
78                                                                                                                      The Quarantine Tapes 096: Daniel Mendelsohn   
287  Homeland Security Lists Gun Stores and Ranges as "Essential"; Australia Closes Gun Stores; Training Under Stay-at-Home Orders: Gun Talk Radio | 3.29.20 Hour 1   
82                                                                      Antisocial Commentary // Childish Gambino’s “This Is America”: The Society of the Spectacle   
45                                                                                                     How Oscar Nominated Screenwriter Kim Krizan Writes: Part Two   
9                                                                               Communication with the Dead (Séances, Mediums, Channelers, Spiritism, Spiritualism)   
135                                                                                                                                     55 - CRUMB w Wayne Federman   
792                                                                                                                                 DARPA Robotics Challenge Review   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [153]:
print(len(final_results_clean))

2656564


In [154]:
final_results_clean.replace(',','', regex=True, inplace=True)
final_results_clean.sample(10)
# final_results_clean.to_csv('final_episode_details.csv', index=False, encoding = 'utf-8')

podcast_id  \
719  1067992218   
113  1288782723   
68   1518666256   
272  1505275450   
170   902067712   
219  1181589165   
956  1212929626   
166   290783428   
66   1114202041   
202   957265404   

                                                                                                                   title  \
719                                                BSN Broncos Podcast: Should Denver make another “big” move? Can they?   
113                                                                       Bonus: From the AAN Annual Meeting (Mon. 5/06)   
68                                                                   Tech heats up the already hot Austin housing market   
272                                                                                             Chapter 10 – Abandonment   
170                                                                                                You Look Good in Blue   
219                                                                                    Where will all that extra oil go?   
956                                         A monkey tried to bang a deer so to the guys this means all birds are female   
166                                                                                                    The Marshall Plan   
66                           WarUp on The WPIAL Recaps State Dual Team and Talks 2A Post-Season with State #1 Jacob Ealy   
202  016: Tim Biggam – Tales from the pit generating trade ideas and a lesson in position sizing with an options veteran   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                       description  \
719                                                                                                     

In [155]:
final_results_clean['title'] = final_results_clean['title'].str.lower()
final_results_clean['description'] = final_results_clean['description'].str.lower()

In [156]:
final_results_clean.sample(10)

podcast_id  \
368    825708806   
670    593432991   
802   1045171376   
94    1184022695   
124   1199902190   
139   1120885936   
67    1292665011   
209    966670774   
2079  1042368254   
12    1493426275   

                                                                                                                                                              title  \
368                                                                                                                             let’s meet etorox with ryta decrypt   
670                                                                                                                                         the ideal muslim family   
802                                                                                                                                          ep. 291 - trump so far   
94                                                                                                                       milo yiannopoulos: past present and future   
124                                                                                                                  96: episode 96:  ecw november to remember 1997   
139                                                                                                                     understanding obsessive compulsive disorder   
67                                                                                                                                  can donald trump be impeached?    
209                                                                                                                            ep. 423: ryan carter // "guide-life"   
2079  middlekauff - 3 and out: pats can bounce back from one "bad" year; pro bowl thoughts; 2018 regular season takeaways; chip kelly's ucla recruiting train wreck   
12                                                                                                                                  episode 54: the roosevelt hotel   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         description  \
368                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             None   
670                                                                                                                                                                        

In [157]:
final_results_clean.replace('\n','', regex=True, inplace=True)

In [158]:
final_results_clean.sample(10)

podcast_id  \
273    688649759   
1618   717428711   
87    1372481697   
130   1501911064   
188   1317356120   
101   1473734049   
11    1436189399   
230    940299283   
83     456417547   
510    979752171   

                                                                                               title  \
273                                                            sbfc 114: lube-bu and the k.y dynasty   
1618                                                                   where the money is 10.14.2014   
87                                                                            ep 103 - claire + phil   
130                                wwe: seth rollins joins the show roman reigns out of wrestlemania   
188                                                        bitcoin atm regulations with bill repasky   
101                                        291: even if this happens you don’t have to make a change   
11    jatcast | prospective study of concussions and health outcomes in high school football players   
230                                                            in case you missed it! - week of 8/28   
83                                                                               s05e01: day million   
510                                       137: the fight against child sex trafficking | tim ballard   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                             description  \
273                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 

In [159]:
# final_results_clean.to_csv('final_episode_details.csv', index=False, encoding = 'utf-8')

In [160]:
final_results_clean.replace('\r',' ', regex=True, inplace=True)
final_results_clean.replace('  ',' ', regex=True, inplace=True)
print(len(final_results_clean))

2656564


In [161]:
## remove all links with http or https as well as any emails xx@xxx
final_results_clean.replace('http\S+|www.\S+|\S*@\S*\s?', '', regex=True, inplace=True)


In [162]:
# remove all hyphens that is not in between words or numbers
# only for the column title and description, because our dates have hyphens
final_results_clean['title'] = final_results_clean['title'].str.replace('-(?!\w)|(?<!\w)-',' ')
final_results_clean['description'] = final_results_clean['description'].str.replace('-(?!\w)|(?<!\w)-',' ')

In [167]:
# remove all puncuations
# only for the column title and description
import string

def remove_punc(x):
    punc = '''!()[]{};:|"\, <>./?@#$%^&*_~•'''
    try:
        for ele in x:
            if ele in punc:
                x = x.replace(ele, " ")
        cleaned = x
    except:
        cleaned = x
    return cleaned

def remove_punc2(x):
    try:
        cleaned = x.strip(string.punctuation)
    except:
        cleaned = x
    return cleaned

final_results_clean['title'] = final_results_clean['title'].map(lambda x: remove_punc(x))
final_results_clean['description'] = final_results_clean['description'].map(lambda x: remove_punc(x))

final_results_clean['title'] = final_results_clean['title'].map(lambda x: remove_punc2(x))
final_results_clean['description'] = final_results_clean['description'].map(lambda x: remove_punc2(x))

In [168]:
final_results_clean.sample(10)

podcast_id  \
65   1101916802   
302  1033048640   
181  1217681421   
31   1458989046   
152   635736811   
505  1159425037   
949   296237493   
163   385998721   
662    75551187   
146   867199020   

                                                                     title  \
65                    ep 164  dr  sarah casey on digital feminist activism   
302                                                 how to stop your anger   
181  dancing with demons with criminal psychologist tim watson-munro    26   
31                                         episode 4   frankenstein  1931    
152                                           episode 233   a people apart   
505  locked on nets   9 22 16   brook lopez to be dealt  with danny leroux   
949            fed will face questions if inflation stays low konstam says   
163                                                        dawn of the ned   
662                                           the new pope and the trinity   
146                                           essentials  27  “homecoming”   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                   description  \
65   on this episode kaite is joined by dr  sarah casey who was awarded a phd in media communication and feminist cultural studies from griffith university  2015   she lectures in screen media and communication at the university of the sunshine coast australia  sarah has published in the areas of media studies feminism and celebrity studies and she is particularly interested in digital feminist activism as well as the role of popular media feminist celebrities in campaigns  sarah is currently finalising a monograph entitled “heroines'” and is the co-author of media and societ

In [112]:
pd.set_option('display.max_colwidth', None)
print(filter_error['description'].to_string())

252    on episode 302 of sleep & relax asmr we go through a brief whispered meditation envisioning we are a mountain. enjoy!  listen on radio public: https://radiopublic.com/sleep-and-relax-asmr-6papm8  ---  enjoy the show? here are our tip jars:  paypal: https://paypal.me/sleepandrelaxasmr  via our website: https://goo.gl/55dj7k  ---  follow us on tingles: https://goo.gl/ev8k8l  email: hello@sleepandrelaxasmr.com  website: www.sleepandrelaxasmr.com--- this episode is sponsored by · anchor: the easiest way to make a podcast.  https://anchor.fm/app--- send in a voice message: https://anchor.fm/sleepandrelaxasmr/message


In [132]:
#making sure string strip doesnt remove hypens
'long-term investments!!'.strip(string.punctuation)


'long-term investments'

In [147]:
"!! don't yell@ at !!@# me!!".strip(string.punctuation)

" don't yell@ at !!@# me"

In [169]:
final_results_clean['title'] = '"' + final_results_clean['title'] + '"'
final_results_clean['description'] = '"' + final_results_clean['description'] + '"'

final_results_clean.sample(5)

podcast_id                                         title  \
130  1218556999     "table talk s2 ep28   matriarch part two"   
14   1541855523                          "how to start anime"   
47   1188406469    "opting out of the great reset   bhop 016"   
331   209377688          "mark levin audio rewind   12 12 19"   
407   652522142  "ep   194  will currie   the country french"   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         description  \
130                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         "table talk for episode 28 season 2  matriarch part two"   
14                                                                                                                                                                                                                                                                                                                                                                                                                                                      "in the newest episode of anime ultra  corbin jesse  amp  christian discuss an age old dilemma how to introduce your friends loved ones to anime  more often than not you'll receive a lot of push back  so we thought we'd help show how we were successful and you too can open the minds of those who snarl their noses at anime blindly  stay weebish fam     this episode is sponsored by · anchor  the easiest way to make a podcast   this podcast  "   
47                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 "koontz   prof     agrarian egghead white guy fisk    author fanatic white guy  "   
331  "on thursday’s mark levin show the democrats on the judic

In [170]:
final_results_clean.to_csv('final_episode_details_with_quotes.csv', index=False, encoding = 'utf-8')

In [171]:
print(len(final_results_clean))

2656564
